<a href="https://colab.research.google.com/github/gtzan/mir_book/blob/master/discretizing_the_frequency_continuum.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import math
import IPython.display as ipd

def make_sine(freq, duration, samplerate=44100):
    """Generates one cycle of a sine wave."""
    t = np.linspace(0, duration, int(samplerate * duration), endpoint=False)
    return np.sin(2 * np.pi * freq * t)

def addsyn(freq, dur, amplist, samplerate=44100):
    """Creates a waveform by summing sine waves (harmonics)."""
    t = np.linspace(0, dur, int(samplerate * dur), endpoint=False)
    output = np.zeros_like(t)
    for i, amp in enumerate(amplist):
        # Add harmonics (multiples of the base frequency)
        output += amp * make_sine(freq * (i + 1), dur, samplerate)
    # Normalize to prevent clipping
    return t, output / np.max(np.abs(output))

# Example: A simple violin-like sound with overtones
# Amplist: [Fundamental, 2nd Harm, 3rd Harm, ...]
t, violin_wave = addsyn(220, 1, [1, 0.263, 0.14, 0.099, 0.209, 0.02, 0.029, 0.077, 0.017, 0.01])

def play_freq(freq, dur):
    amplist = [1, 0.263, 0.14, 0.099, 0.209, 0.02, 0.029, 0.077, 0.017, 0.01]
    t, audio = addsyn(freq, dur, amplist, samplerate=44100)
    return 0.5 * audio


ipd.Audio(violin_wave, rate=44100)


In [2]:
def karplus_strong(frequency, duration, sample_rate=44100, decay=0.996):
    """
    Generates a string-like sound at a specific frequency.
    """
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    # 1. Calculate delay line length (N) based on desired frequency
    N = int(sample_rate / frequency)

    # 2. Initialize the delay line with noise (the "pluck")
    # This represents the initial energy transferred to the string
    ring_buffer = np.random.uniform(-1, 1, N)

    # 3. Generate the output signal
    num_samples = int(duration * sample_rate)
    audio = np.zeros(num_samples)

    for i in range(num_samples):
        # The current sample is the first in the buffer
        audio[i] = ring_buffer[0]

        # 4. Filter: Average the first two samples and apply decay
        # This simulates high-frequency energy loss over time
        new_sample = decay * 0.5 * (ring_buffer[0] + ring_buffer[1])

        # 5. Update the buffer (remove first, append new)
        ring_buffer = np.roll(ring_buffer, -1)
        ring_buffer[-1] = new_sample

    return t, audio

# --- Usage in Notebook ---
fs = 44100
# Play an A4 note (440 Hz) for 2 seconds
t, note_a4 = karplus_strong(440, 2, sample_rate=fs)

# Use IPython to display the player widget
ipd.Audio(note_a4, rate=fs)


def pluck_freq(freq, dur):
    t, audio = karplus_strong(freq, dur, sample_rate=44100)
    return audio


In [3]:
drone = play_freq(220, 6)
pentatonic_scale_freqs = [440, 493.88, 554.37, 659.25, 739.99, 880]
melody = []
for freq in pentatonic_scale_freqs:
    audio = pluck_freq(freq, 0.5)
    melody.append(audio)

for freq in pentatonic_scale_freqs[::-1]:
    audio = pluck_freq(freq, 0.5)
    melody.append(audio)
melody = np.concatenate(melody)
ipd.Audio(drone + melody, rate=44100)


In [104]:
def play_freqs_with_drone(freqs, durations, mode = "up", tempo=120, instrument="organ"):
  melody = []
  duration = 0
  qn_dur = 60 / tempo
  if (mode == "up")or(mode=="up_down"):
    for freq, dur in zip(freqs, durations):
      if (instrument=="organ"):
        audio = play_freq(freq, dur * qn_dur)
      else:
        audio = pluck_freq(freq, dur * qn_dur)
      duration += dur * 0.5
      melody.append(audio)

  if ((mode == "up_down")or(mode == "down")):
    for freq, dur in zip(freqs[::-1], durations[::-1]):
        if (instrument=="organ"):
          audio = play_freq(freq, dur * qn_dur)
        else:
          audio = pluck_freq(freq, dur * qn_dur)
        duration += dur * 0.5
        melody.append(audio)
  melody = np.concatenate(melody)
  srate = 44100
  drone = play_freq(freqs[0]/2.0, len(melody) / srate)
  return 0.5 * drone + melody

pentatonic_scale_freqs = np.array([440, 493.88, 554.37, 659.25, 739.99, 880])
durations = [0.5, 0.5, 1, 0.5, 0.5, 1]


ipd.Audio(play_freqs_with_drone(pentatonic_scale_freqs,
          durations, mode="up_down"),rate=44100)


In [106]:
def midi_to_hz(midi_note_number):
    """
    Convert a MIDI note number to its frequency in Hertz (Hz).
    Uses A4 (MIDI note 69) as the 440 Hz reference.
    """
    # The number of semitones from A4 (MIDI note 69)
    semitones = midi_note_number - 69
    # Calculate the frequency
    frequency = 440 * (2**(semitones / 12))
    return frequency

intervals = [-5, -5, -5, 0, 7, 5, 4, 2, 12, 7]
pitches = [55 + i for i in intervals]
freqs = [midi_to_frequency(p) for p in pitches]
print(freqs)
durations = [1.0/3.0, 1.0/3.0, 1.0/3, 2, 2, 1.0/3.0, 1.0/3.0, 1.0/3.0, 2, 1]
star_wars_theme = play_freqs_with_drone(freqs, durations, mode="up", instrument="organ", tempo=100)
ipd.Audio(star_wars_theme, rate=44100)

[146.8323839587038, 146.8323839587038, 146.8323839587038, 195.99771799087463, 293.6647679174076, 261.6255653005986, 246.94165062806206, 220.0, 391.99543598174927, 293.6647679174076]


In [107]:
import random
random.shuffle(pentatonic_scale_freqs)
random_pentatonic = pentatonic_scale_freqs
durations = np.ones(len(random_pentatonic))
print(random_pentatonic)
ipd.Audio(play_freqs_with_drone(random_pentatonic, durations), rate=44100)

[493.88 554.37 659.25 880.   739.99 440.  ]


In [108]:
# Pythagorean tuning

freqs = np.zeros((13))
freqs[0] = 220    #A
freqs[1] = (3.0/2.0) * freqs[0]          #E
freqs[2] = (3.0/2.0) * freqs[1] / 2.0    #B
freqs[3] = (3.0/2.0) * freqs[2]          # F#
freqs[4] = (3.0/2.0) * freqs[3] / 2.0    # C#
freqs[5] = (3.0/2.0) * freqs[4]
freqs[6] = (3.0/2.0) * freqs[5] / 2.0
freqs[7] = (3.0/2.0) * freqs[6] / 2.0
freqs[8] = (3.0/2.0) * freqs[7]
freqs[9] = (3.0/2.0) * freqs[8] / 2.0
freqs[10] = (3.0/2.0) * freqs[9]
freqs[11] = (3.0/2.0) * freqs[10] / 2.0
freqs[12] = (3.0/2.0) * freqs[11]
#freqs[12] = 440
freqs = [f for f in freqs if f != 0]
print(freqs)
freqs.sort()
print(freqs)
durations = np.ones(len(freqs))
ipd.Audio(play_freqs_with_drone(freqs, durations), rate=44100)



[np.float64(220.0), np.float64(330.0), np.float64(247.5), np.float64(371.25), np.float64(278.4375), np.float64(417.65625), np.float64(313.2421875), np.float64(234.931640625), np.float64(352.3974609375), np.float64(264.298095703125), np.float64(396.4471435546875), np.float64(297.3353576660156), np.float64(446.00303649902344)]
[np.float64(220.0), np.float64(234.931640625), np.float64(247.5), np.float64(264.298095703125), np.float64(278.4375), np.float64(297.3353576660156), np.float64(313.2421875), np.float64(330.0), np.float64(352.3974609375), np.float64(371.25), np.float64(396.4471435546875), np.float64(417.65625), np.float64(446.00303649902344)]


In [109]:
print(freqs[-1])
octave = play_freq(2*freqs[0], 1)
pythagorean_octave = play_freq(freqs[-1], 1)
drone = play_freq(freqs[0]/2.0, 5)
audio = np.concatenate([octave,pythagorean_octave, octave, pythagorean_octave, pythagorean_octave])
ipd.Audio(drone + audio, rate=44100)



446.00303649902344


In [110]:
import math

def midi_to_pythagorean_hz(midi_note, ref_note=69, ref_hz=440.0):
    """
    Converts a MIDI note number to frequency using Pythagorean tuning.
    Calculates the note's position on the circle of fifths relative to A.
    """
    # 1. Circle of Fifths positions relative to A (0)
    # Mapping MIDI note classes (0-11) to their 'fifth' distance from A
    # A=0, E=1, B=2, F#=3, C#=4, G#=5, D#=6, A#=7, F= -3, C= -2, G= -1
    # We use a standard 12-note chromatic arrangement centered around A.
    note_to_fifths = {
        9: 0,   # A
        4: 1,   # E
        11: 2,  # B
        6: 3,   # F#
        1: 4,   # C#
        8: 5,   # G#
        3: 6,   # D# / Eb (The "Wolf" boundary is often here)
        10: -5, # Bb / A#
        5: -4,  # F
        0: -3,  # C
        7: -2,  # G
        2: -1   # D
    }

    # 2. Get the note class (0-11) and octave
    note_class = midi_note % 12
    octave_shift = (midi_note // 12) - (ref_note // 12)

    # 3. Calculate distance in fifths from the reference A
    n_fifths = note_to_fifths[note_class]

    # 4. Pythagorean Formula: f = ref * (3/2)^n * (1/2)^octave_adjustment
    # We must normalize the result into the correct octave.
    # Each +1 fifth is ~702 cents; we subtract octaves to stay in the 0-1200 cent range.
    raw_ratio = (3/2) ** n_fifths

    # Normalize the ratio to be within [1.0, 2.0) relative to the root octave
    while raw_ratio >= 2.0:
        raw_ratio /= 2.0
    while raw_ratio < 1.0:
        raw_ratio *= 2.0

    # 5. Apply the specific octave from the MIDI note number
    frequency = ref_hz * raw_ratio * (2 ** octave_shift)

    # Correction: If the note class is 'lower' than A in the octave (0-8),
    # it naturally belongs to the 'current' MIDI octave, but our ratio
    # calculation is relative to A.
    if note_class < 9:
        frequency /= 2.0

    return frequency

# --- Example Usage ---
notes = [60, 69, 71] # C4, A4, B4
for n in notes:
    print(f"MIDI {n}: {midi_to_pythagorean_hz(n):.2f} Hz")


MIDI 60: 260.74 Hz
MIDI 69: 440.00 Hz
MIDI 71: 495.00 Hz


In [111]:
start_pitch = 51
intervals = [-5, -5, -5, 0, 7, 5, 4, 2, 12, 7]
pitches = [start_pitch + i for i in intervals]
freqs = [midi_to_pythagorean_hz(p) for p in pitches]
print(freqs)
durations = [1.0/3.0, 1.0/3.0, 1.0/3, 2, 2, 1.0/3.0, 1.0/3.0, 1.0/3.0, 2, 4]
star_wars_theme = play_freqs_with_drone(freqs, durations, mode="up", tempo=100)
ipd.Audio(star_wars_theme, rate=44100)

[115.88477366255145, 115.88477366255145, 115.88477366255145, 156.62109375, 231.7695473251029, 208.828125, 195.55555555555554, 173.82716049382714, 313.2421875, 231.7695473251029]


In [113]:
start_pitch = 51
intervals = [0, 2, 4, 0, 0, 2, 4, 0, 4]
pitches = [start_pitch + i for i in intervals]
freqs = [midi_to_pythagorean_hz(p) for p in pitches]
print(freqs)
durations = [1, 1, 1, 1, 1, 1, 1, 1, 4]
brother_john_theme = play_freqs_with_drone(freqs, durations, mode="up", tempo=100)
ipd.Audio(brother_john_theme, rate=44100)

[156.62109375, 173.82716049382714, 195.55555555555554, 156.62109375, 156.62109375, 173.82716049382714, 195.55555555555554, 156.62109375, 195.55555555555554]


1.4798079440177243

1.3333333333333333

In [116]:
def interval(freq1, freq2):
    data1 = play_freq(freq1, dur = 1.0)
    data2 = play_freq(freq2, dur = 1.0)
    sum_data = (data1+data2) * 0.5
    data = np.hstack([data1, data2, sum_data, sum_data])
    return data

In [117]:
ipd.Audio(interval(220, 440), rate=44100)

In [119]:
print("3.0/2.0=1.5 ratio (just intonation 5th)")
ipd.display(ipd.Audio(interval(220, 3.0/2.0 * 220), rate=44100))
ratio = np.power(np.power(2.0, 1.0/12.0),7.0)
print("Equal temperement fifth %f" % ratio)
ipd.display(ipd.Audio(interval(220, ratio * 220), rate=44100))

3.0/2.0=1.5 ratio (just intonation 5th)


Equal temperement fifth 1.498307


In [124]:
print('5.0/4.0=1.25 ratio (just intonation major third)')
ipd.display(ipd.Audio(interval(220, 5.0/4.0 * 220), rate=44100))

ratio =  81.0/64.0
print("Pythgorean major third %f " % ratio)
ipd.display(ipd.Audio(interval(220, 81.0/64.0 * 220), rate=44100))

print("Equal temperement major third %f" % ratio)
ratio = np.power(np.power(2.0, 1.0/12.0),4.0)
ipd.display(ipd.Audio(interval(220, ratio * 220), rate=44100))

5.0/4.0=1.25 ratio (just intonation major third)


Pythgorean major third 1.265625 


Equal temperement major third 1.265625


In [126]:
# random ratio
ipd.display(ipd.Audio(interval(220, 1.22 * 220), rate=44100))